In [1]:
#connecting to the api

from requests import Request, Session
from requests.exceptions import ConnectionError, Timeout, TooManyRedirects
import json

url = 'https://pro-api.coinmarketcap.com/v1/cryptocurrency/listings/latest'
parameters = {
  'start':'1',
  'limit':'5000',
  'convert':'USD'
}
headers = {
  'Accepts': 'application/json',
  'X-CMC_PRO_API_KEY': '6c693fc0-53b1-4dc3-993c-0d0d5f9a978b',
}

session = Session()
session.headers.update(headers)

try:
  response = session.get(url, params=parameters)
  data = json.loads(response.text)
  print(data)
except (ConnectionError, Timeout, TooManyRedirects) as e:
  print(e)

{'status': {'timestamp': '2023-07-28T21:24:15.294Z', 'error_code': 0, 'error_message': None, 'elapsed': 76, 'credit_count': 25, 'notice': None, 'total_count': 9933}, 'data': [{'id': 1, 'name': 'Bitcoin', 'symbol': 'BTC', 'slug': 'bitcoin', 'num_market_pairs': 10377, 'date_added': '2010-07-13T00:00:00.000Z', 'tags': ['mineable', 'pow', 'sha-256', 'store-of-value', 'state-channel', 'coinbase-ventures-portfolio', 'three-arrows-capital-portfolio', 'polychain-capital-portfolio', 'binance-labs-portfolio', 'blockchain-capital-portfolio', 'boostvc-portfolio', 'cms-holdings-portfolio', 'dcg-portfolio', 'dragonfly-capital-portfolio', 'electric-capital-portfolio', 'fabric-ventures-portfolio', 'framework-ventures-portfolio', 'galaxy-digital-portfolio', 'huobi-capital-portfolio', 'alameda-research-portfolio', 'a16z-portfolio', '1confirmation-portfolio', 'winklevoss-capital-portfolio', 'usv-portfolio', 'placeholder-ventures-portfolio', 'pantera-capital-portfolio', 'multicoin-capital-portfolio', 'par

In [2]:
type(data)

dict

In [7]:
%pip install psycopg2
import psycopg2 as ps
import pandas as pd
pd.set_option('display.max_columns', None)

In [ ]:
def connect_to_database(host_name, dbname, port, username, password):
    try :
        connection = ps.connect(host=host_name, database=dbname, user=username, password=password, port=port)

    except ps.OperationalError as e:
        raise e
        
    else:
        print('Connection Successful')
        
    return connection

In [ ]:
#creating the table for the database

def create_table(curr):
    create_database_table = ("""CREATE TABLE IF NOT EXISTS cryptodata(
                    id INTEGER NOT NULL PRIMARY KEY, 
                    name TEXT NOT NULL,
                    symbol TEXT NOT NULL,
                    slug TEXT NOT NULL,
                    num_market_pairs INTEGER NOT NULL,
                    date_added DATETIME NOT NULL,
                    tags TEXT NOT NULL,
                    max_supply VARCHAR(255),
                    circulating_supply VARCHAR(255),
                    total_supply BIGINT,
                    quote.USD.market_cap VARCHAR(255),
                    quote.USD.market_cap_dominance FLOAT,
                    quote.USD.fully_diluted_market_cap VARCHAR(255),
                    quote.USD.tvl NULL,
                    quote.USD.last_updated DATETIME,
                    platform.id FLOAT,
                    platform.name VARCHAR(255),
                    platform.symbol VARCHAR(255),
                    platform.slug VARCHAR(255),
                    platform.token_address VARCHAR(255)
                    )""")

    curr.execute(create_database_table)

In [ ]:
#insert command
def insert_into_table(curr,id,name,symbol,slug,num_market_pairs,date_added,tags,max_supply,circulating_supply,total_supply,quote.USD.market_cap, quote.USD.market_cap_dominance, quote.USD.fully_diluted_market_cap,quote.USD.tvl, quote.USD.last_updated, platform.id, platform.name, platform.symbol,  platform.slug, platform.token_address):
    insert_into_cryptodata = ("""INSERT INTO cryptodata (id,name,symbol,slug, num_market_pairs,date_added,tags,max_supply, circulating_supply, total_supply, quote.USD.market_cap, quote.USD.market_cap_dominance, quote.USD.fully_diluted_market_cap,quote.USD.tvl, quote.USD.last_updated, platform.id, platform.name, platform.symbol,  platform.slug, platform.token_address) 
                                 VALUES(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s);""")

    rows_to_insert = (id,name,symbol,slug,num_market_pairs,date_added,tags,max_supply,circulating_supply,total_supply,quote.USD.market_cap, quote.USD.market_cap_dominance, quote.USD.fully_diluted_market_cap,quote.USD.tvl, quote.USD.last_updated, platform.id, platform.name, platform.symbol,  platform.slug, platform.token_address) 
    curr.execute(insert_into_cryptodata, rows_to_insert)
    

In [ ]:
#updating row if row exists

def update_row(curr,id,name,symbol,slug, num_market_pairs,date_added,tags,max_supply, circulating_supply, total_supply, quote.USD.market_cap, quote.USD.market_cap_dominance, quote.USD.fully_diluted_market_cap,quote.USD.tvl, quote.USD.last_updated, platform.id, platform.name, platform.symbol,  platform.slug, platform.token_address):
    query = ("""UPDATE cryptodata
                 SET name = %s,
                     symbol = %s,
                     slug = %s,
                     num_market_pairs = %s,
                     date_added = %s,
                     tags = %s,
                     max_supply = %s,
                     circulating_supply = %s,
                     total_supply = %s,
                     quote.USD.market_cap = %s,
                     quote.USD.market_cap_dominance = %s,
                     quote.USD.fully_diluted_market_cap = %s,
                     quote.USD.tvl = %s,
                     quote.USD.last_updated = %s,
                     platform.id = %s,
                     platform.name = %s,
                     platform.symbol = %s,
                     platform.slug = %s,
                     platform.token_address = %s
                     WHERE id = %s;""")

    variables_to_update = (name,symbol,slug, num_market_pairs,date_added,tags,max_supply, circulating_supply, total_supply, quote.USD.market_cap, quote.USD.market_cap_dominance, quote.USD.fully_diluted_market_cap,quote.USD.tvl, quote.USD.last_updated, platform.id, platform.name, platform.symbol,  platform.slug, platform.token_address)
    curr.execute(query, variables_to_update)

In [ ]:
#check if row exists

def check_row_exists(curr, id):
    query = ("""SELECT id FROM CRYPTODATA WHERE id = %s""")
    curr.execute(query, (id,))

    return curr.fetchone() is not None 

In [ ]:
def append_from_dataframe_to_database(curr,data):
    for i, row in data.iterrows():
        insert_into_table(curr,row['id'], row['name'], row['symbol'], row['slug'], row['num_market_pairs'], row['date_added'], row['tags'], row['max_supply'],row['circulating_supply'],row['total_supply'],row['quote.USD.market_cap'], row['quote.USD.market_cap_dominance'], row['quote.USD.fully_diluted_market_cap'],row['quote.USD.tvl'],row['quote.USD.last_updated'],row['platform.id'],row['platform.name'],row['platform.symbol'],row['platform.slug'],row['platform.token_address'])

In [ ]:
#updating the database

def update_database(curr,data):
    temp_dataframe = pd.DataFrame(columns=['id', 'name', 'symbol','slug', 'num_market_pairs', 'date_added', 'tags', 'max_supply', 'circulating_supply', 'total_supply', 'quote.USD.market_cap', 'quote.USD.market_cap_dominance', 'quote.USD.fully_diluted_market_cap', 'quote.USD.tvl', 'quote.USD.last_updated', 'platform.id', 'platform.name', 'platform.symbol', 'platform.slug', 'platform.token_address'])

    for i, row in data.iterrows():
            #if row already exists
            if check_row_exists():
                update_row(curr,row['id'], row['name'], row['symbol'], row['slug'], row['num_market_pairs'], row['date_added'], row['tags'], row['max_supply'],row['circulating_supply'],row['total_supply'],row['quote.USD.market_cap'], row['quote.USD.market_cap_dominance'], row['quote.USD.fully_diluted_market_cap'],row['quote.USD.tvl'],row['quote.USD.last_updated'],row['platform.id'],row['platform.name'],row['platform.symbol'],row['platform.slug'],row['platform.token_address'])

            #if row doesn't exists
            else: 
                temp_dataframe = temp_dataframe.append(row)
            
    return temp_dataframe

In [5]:
pd.json_normalize(data['data'])

id               name  symbol               slug  num_market_pairs  \
0         1            Bitcoin     BTC            bitcoin             10377   
1      1027           Ethereum     ETH           ethereum              7190   
2       825        Tether USDt    USDT             tether             58003   
3        52                XRP     XRP                xrp              1014   
4      1839                BNB     BNB                bnb              1545   
...     ...                ...     ...                ...               ...   
4995  20581      Learning Star   LSTAR      learning-star                 6   
4996  25483        Sheikh Pepe  SKPEPE        sheikh-pepe                 2   
4997  21736             Kondux    KNDX             kondux                 1   
4998  23036         Liquid CRO    LCRO       veno-finance                 7   
4999  18444  Giresunspor Token     GRS  giresunspor-token                 2   

                    date_added  \
0     2010-07-13T00:00:00.000Z   
1     2015-08-07T00:00:00.000Z   
2     2015-02-25T00:00:00.000Z   
3     2013-08-04T00:00:00.000Z   
4     2017-07-25T00:00:00.000Z   
...                        ...   
4995  2022-06-13T14:55:05.000Z   
4996  2023-05-21T08:03:19.000Z   
4997  2022-09-07T11:55:10.000Z   
4998  2023-02-07T06:23:16.000Z   
4999  2022-03-01T04:07:05.000Z   

                                                   tags    max_supply  \
0     [mineable, pow, sha-256, store-of-value, state...  2.100000e+07   
1     [pos, smart-contracts, ethereum-ecosystem, coi...           NaN   
2     [payments, stablecoin, asset-backed-stablecoin...           NaN   
3     [medium-of-exchange, enterprise-solutions, arr...  1.000000e+11   
4     [marketplace, centralized-exchange, payments, ...           NaN   
...                                                 ...           ...   
4995                                                 []  0.000000e+00   
4996                                                 []  8.888889e+09   
4997                                                 []  1.000000e+09   
4998                                                 []           NaN   
4999                                                 []  1.000000e+06   

      circulating_supply          total_supply  ...  quote.USD.market_cap  \
0           1.944169e+07              19441687  ...          5.706189e+11   
1           1.201888e+08         120188810.897  ...          2.255619e+11   
2           8.382178e+10    86706257841.391861  ...          8.382571e+10   
3           5.269385e+10           99988556423  ...          3.752403e+10   
4           1.538557e+08      153855711.765023  ...          3.731053e+10   
...                  ...                   ...  ...                   ...   
4995        0.000000e+00             600369231  ...          0.000000e+00   
4996        0.000000e+00            8888888888  ...          0.000000e+00   
4997        0.000000e+00  9498293966312.949219  ...          0.000000e+00   
4998        0.000000e+00              15893117  ...          0.000000e+00   
4999        0.000000e+00                599637  ...          0.000000e+00   

      quote.USD.market_cap_dominance  quote.USD.fully_diluted_market_cap  \
0                            48.1852                        6.163559e+11   
1                            19.0477                        2.255619e+11   
2                             7.0787                        8.671032e+10   
3                             3.1689                        7.121141e+10   
4                             3.1509                        3.731053e+10   
...                              ...                                 ...   
4995                          0.0000                        7.187690e+05   
4996                          0.0000                        6.124890e+03   
4997                          0.0000                        1.454339e+06   
4998                          0.0000                        9.905907e+05   
4999         

In [ ]:
#Main 

#database information
host_name = 'amazonpostgresql'
dbname = 'apiProject'
port = '1234'
username = 'dummyUsername'
password = 'dummyPass'
connection = None

#establish connection to database
connection = connect_to_database(host_name, dbname, port, username, password)
curr = connection.cursor()

In [ ]:
#creating a table in the database
create_table(curr)

In [ ]:
#updating existing data in the database
new_crypto_dataframe = update_database(curr,data)
connection.commit()

In [ ]:
#inserting new data in the database
append_from_dataframe_to_database(curr,new_crypto_dataframe)
connection.commit()